## Importing the necessary libraries

In [ ]:
import pandas as pd
import numpy as np
import glob
from datetime import datetime
import os
import re
import string
import nltk

from collections import Counter
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

import seaborn as sns
import matplotlib.pyplot as plt

from datetime import datetime
from datetime import timedelta
from datetime import date

from sklearn.feature_extraction.text import CountVectorizer
import scipy.sparse as ss


from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:

!pip install corextopic

from corextopic import corextopic as ct
from corextopic import vis_topic as vt
#vt.vis_rep(anchored_topic_model, column_label=words, prefix='ZocDoc')

from nltk.tokenize import TweetTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.corpus import wordnet

In [ ]:
# Setting column width and dataframe display size
pd.set_option("max_colwidth", 300)
pd.set_option("max_columns", 30)
pd.set_option("max_rows", 10000)


In [ ]:
#print(dfx.loc[14]['clean_text'])

## LDA function

In [ ]:
# LDA function
def func_lda(dfs):
  import gensim
  from gensim.utils import simple_preprocess
  import nltk
  nltk.download('stopwords')
  from nltk.corpus import stopwords
  stop_words = stopwords.words('english')
  # stop_words.extend(['from', 'subject', 're', 'edu', 'use'])

  def sent_to_words(sentences):
    for sentence in sentences:
      # deacc=True removes punctuations
      yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))
  def remove_stopwords(texts):
    return [[word for word in simple_preprocess(str(doc)) 
              if word not in stop_words] for doc in texts]
  def remove_numbs(text2):    # to remove numbers
    return [[word for word in word_set 
              if not word.isdigit()] for word_set in text2]

  data = dfs.values.tolist()
  data_words = list(sent_to_words(data))
  print(type(data_words))
  print("simple output:")
  print(data_words)
  
  # remove stop words
  data_words = remove_stopwords(data_words)
  #print("After removing stopwords:")
  #print(data_words)
  data_words    =  remove_numbs(data_words)           

  print(data_words[:1][0][:30])
  
  
  
  import gensim
  from gensim.models import CoherenceModel
  import gensim.corpora as corpora
  # Create Dictionary

  id2word = corpora.Dictionary(data_words)

  # Create Corpus
  texts = data_words
  # Term Document Frequency
  corpus = [id2word.doc2bow(text) for text in texts]
  # View
  print("corpus output:")
  print(corpus[:1][0][:30])

  from pprint import pprint

  # number of topics
  num_topics = 10

  # Build LDA model
  lda_model = gensim.models.LdaMulticore(corpus=corpus,
                                        id2word=id2word,
                                        num_topics=num_topics)

  # Print the Keyword in the 10 topics
  print("topics:")
  pprint(lda_model.print_topics())
  doc_lda = lda_model[corpus]
  
  return (num_topics,id2word,corpus,lda_model)


## Unsupervised CoRex function

In [ ]:
def corex_func(df2):
  #from sklearn.feature_extraction.text import CountVectorizer
  cv = CountVectorizer(max_df=0.95, min_df=2, stop_words='english')
  dtm = cv.fit_transform(df2['lemma_2'])

  # Get words that label the columns (needed to extract readable topics and make anchoring easier)
  words = list(np.asarray(cv.get_feature_names()))

  print(words)

  print(type(words))
  
  not_digit_inds = [ind for ind, word in enumerate(words) if not word.isdigit()]
  dtm = dtm[:, not_digit_inds]
  words    = [word for ind,word in enumerate(words) if not word.isdigit()]

  print(dtm.shape)
  
  anchors = [] #without seed words
  anchors = [
      [a for a in topic if a in words]
      for topic in anchors
          ]

  model = ct.Corex(n_hidden=14, seed=51)
  model = model.fit(
      dtm,
      words=words,
      anchors = anchors,
      anchor_strength=10)

  for i, topic_ngrams in enumerate(model.get_topics(n_words=20)):
      topic_ngrams = [ngram[0] for ngram in topic_ngrams if ngram[1] > 0]
      print("Topic #{}: {}".format(i+1, ", ".join(topic_ngrams)))


  

In [ ]:
#symptoms,causes,transmission,prevention,testing,treatment,mental_health,economic_impact,vaccination,vaccination_opposition, policies,children_education,government

## Semi-supervised CoRex function

In [ ]:
# Topics and Anchor words
#Set2

anchor_words = [
#1 symptoms =  
['cold', 'cough', 'flu',  'fever', 'headache', 'sore', ' throat', 'muscle', 'breath', 'lungs',
             'nausea', 'vomit', 'diarrhea', 'fever', 'fatigue', 'tired', 'symptom','mild','disease','reinfection', 'illness'],
#2 prevention = 
['mask', 'sanitizer', 'distance', 'glove', 'ppe', 'kit', 'n95', 'quarantine' ,'wash', 'isolation', 'wearamask', 'maskup', 'kn95'],
#3 testing = 
['test', 'positive', 'negative', 'oximeter', 'pcr', 'rtpcr', 'detect','report'],
#4 treatment = 
['antibody','sotrovimab','therapy','antigen','bamlanivimab','etesevimab','casirivimab','imdevimab','regen','sotrovimab',
             'tixagevimab','cilgavimab','evusheld','medication','acetaminophen','ibuprofen','pharmacy','capsule','tablet','ayurveda',
             'reliever','ivermectin','pill', 'injection', 'doctor', 'mrna', 'monoclonal', 'icu'],

#5 economic_impact =  
['economic', 'stock', 'market', 'layoff', 'unemployed', 'job', 'interview', 'poor', 'wage', 'salary', 'finance', 'closure',
                   'price','investor', 'crypto', 'bitcoin', 'inflation'],
#6 Travel = 
['travel', 'flight', 'cab', 'train', 'bus', 'metro', 'publictransport', 'holiday', 'vacation', 'passenger', 'arrival', 'departure', 
          'cruise', 'ship', 'airport','drive'],
#7 vaccination = 
['pfizer','biontech','johnson','vaccine','moderna','niaid','covishield','covaxin','jabbed','vaxxed','vax','protection','booster',
               'vaccinate', 'getboostednow', 'dose', 'sciencewins', 'getvaccinatednow', 'covaxin4kids', 'superimmunity'],
#8 vaccination_opposition =
['conspiracy','unvaccinated','chip','anti','antivax','vaccinekills','novaccincation','justsayno',
                          'boycottvaccine','saynotovaccine', 'vaccinesideeffects', 'covidiots', 'donotcomply'],
#9 policies = 
['mandate','rule','regulation','policy','lockdown','suspend','ban', 'mandatory','restriction','impose','guideline','measure', 
            'safetyfirst', 'letitrip', 'vaccinepassports'],
#10 causes = 
['party','crowd','marriage','gathering','concert','game','event','movie','wedding','function','marathon','conference',
          'match','football'],
#11 transmission = 
['contagious','spread','transmit','touch','case','infect','mutate', 'mutation', 'outbreak','airborne','droplets','superspreader', 'death'],
#12 children_education = 
['school','college','children','education','college','university','maketerm1hybird','cancelterm1','exam', 'institute', 'semester',
		       'teacher', 'class', 'classroom'],
#13 government = 
['official','federal','state','president','minister','government','misinformation','authority', 'pm', 'premier'],

#14 mental_health = 
['stress', 'depress', 'lonely', 'sad', 'anxiety', 'alert', 'panic']
]

all_topics = ['symptoms','prevention', 'testing', 'treatment', 'economic_impact', 'travel', 'vaccination', 'vaccination_opposition', 
 'policies', 'causes', 'transmission', 'children_education', 'government', 'mental_health']

# Semi Supervised CoRex function

def corex_func_anchor(df2):
  #from sklearn.feature_extraction.text import CountVectorizer
  cv = CountVectorizer(max_df=0.95, min_df=2, stop_words='english')
  dtm = cv.fit_transform(df2['lemma_2'])
  print(type(dtm))
  print(dtm.shape, "\n")
  # Get words that label the columns (needed to extract readable topics and make anchoring easier)
  words = list(np.asarray(cv.get_feature_names()))
  
  not_digit_inds = [ind for ind,word in enumerate(words) if not word.isdigit()]
  dtm = dtm[:, not_digit_inds]
  words    = [word for ind,word in enumerate(words) if not word.isdigit()]

  print(dtm.shape)
  print("\n")
  #print(dtm.head)

  
  anchors = [
      [a for a in topic if a in words]
      for topic in anchor_words
          ]
  print("THESE ARE THE ANCHORS")
  print(anchors)

  model = ct.Corex(n_hidden=len(all_topics), seed=37)
  model = model.fit(
      dtm,
      words=words,
      anchors = anchors,
      anchor_strength=10)

  for i, topic_ngrams in enumerate(model.get_topics(n_words=30)):
      topic_ngrams = [ngram[0] for ngram in topic_ngrams if ngram[1] > 0]
      print("Topic #{}: {}".format(i+1, ", ".join(topic_ngrams)))
  
  vt.vis_rep(model, column_label=words)

  #Total Correlation score for each topic on all tweets
  print(model.tcs)
  print("\n")

  print(model.p_y_given_x)
  print("\n")

  #probability a document (row) belongs to a certain topic where 0 is 100% probability
  #The closer to zero the more likely that row/review/document belongs to that topic
  
  #print(model.log_p_y_given_x)
  
  log_table = model.log_p_y_given_x
  return log_table, words 

  #print("\n")


  
  #Here model is the the corex model defined above, we extract the log_z score, 
  #which represents the strength of a topic relative to the document (long string of concatnated tweets) 

  #variable a holds the object below
  ''' 
  a = model.log_z

  #Defining the schema for the dataframe which builds on tabluating the results for topic strength
  twt = list(df2['id'])
  col = ['symptoms','prevention','testing','treatment','mental_health','economic_impact','vaccination', 
         'vaccination_opposition', 'policies', 'causes', 'transmission', 'children+Education', 'government']

  #Define the dataframe with above schema and fill in the topic strength values 'a' for the corresponding topics and twitter handles
  cor = pd.DataFrame(a, columns=col)

  cor['id'] = list(df2['id'])

  cor

  return cor
  '''



In [ ]:
'''
path = "/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv"
dfy = pd.read_csv(path, engine='python')
dfy.shape
'''


'\npath = "/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv"\ndfy = pd.read_csv(path, engine=\'python\')\ndfy.shape\n'

## Reading and clubbing the weekly csv files into one dataframe

In [ ]:

#dft = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
#dft = pd.DataFrame(columns = dft.columns)
#dft.head(1000)


In [ ]:
df = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader_OP/V_Sentiment_Week1.csv", engine ='python')
df.columns
#df = pd.DataFrame(columns = df.columns + )

Index(['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos'],
      dtype='object')

In [ ]:
df.head()

created_at                   id  \
0  Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1  Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2  Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3  Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4  Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos  
0    0.7253  0.000  0.7

In [ ]:

#df = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
df = pd.DataFrame(columns = ['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos', 'week'])


interesting_files = glob.glob("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader_OP/*.csv")  
#print(len(interesting_files))
number_of_files = len(interesting_files)

for week in range(1, number_of_files+1):    # number_of_files
  path = "/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader_OP/V_Sentiment_Week" + str(week) + ".csv"
  dfx = pd.read_csv(path, engine= 'python')
  dfx['week'] = "week_" + str(week)
  df = pd.concat([df, dfx], ignore_index=True)  

df['id'] = df['id'].astype(str)
df.shape

(441675, 11)

In [ ]:
one_to_hundred = pd.Series(range(1,len(df)+1))
df['UIN'] = one_to_hundred

In [ ]:
df.tail()

created_at                   id  \
441670  Tue Feb 01 05:02:03 +0000 2022  1488377083076263936   
441671  Tue Feb 01 05:02:09 +0000 2022  1488377106992033797   
441672  Tue Feb 01 05:03:18 +0000 2022  1488377396805836803   
441673  Tue Feb 01 05:02:19 +0000 2022  1488377149308481542   
441674  Tue Feb 01 05:04:44 +0000 2022  1488377756526206976   

                                                                                                                                                                                                                                                           text  \
441670                                                                                                                                  Ivermectin Has 'Antiviral Effect' Against Omicron And All Other 'Mutant Strains' Of Covid-19\n\nhttps://t.co/t7zACadkNP   
441671                                                                                                                     @realDailyWire CORRECTED-Japan's Kowa says ivermectin showed 'antiviral effect' against Omicron in research\nhttps://t.co/gZeVT8t9CZ   
441672                                                                                                                                                         2 new omicron symptoms you won’t realize are from COVID https://t.co/9yweO1KuKG via @DeseretNews   
441673                                                                   COVID-19 Omicron variant now dominant in Italy, health body says - Reuters\n\nPublished At :2022-01-14T12:09:00Z\nSource:"#Reuters"\n\nhttps://t.co/srhWh9hcLW https://t.co/QqSpqPYMl2   
441674  Good grief . . . Where’s the logic in this @ShabirMadh @Tuliodna . . . ‘South Africans who test positive for the coronavirus but show no symptoms of Covid-19 will no longer be required to self-isolate’ \n#covid #Omicron \n\nhttps://t.co/OwHxpGuQZz   

             user_id  \
441670  9.821061e+17   
441671  2.855330e+09   
441672  1.521389e+08   
441673  1.441500e+18   
441674  1.218511e+08   

                                                                                                                                                                                                                                                omicron_tweets  \
441670                                                                                                                                 ivermectin has 'antiviral effect' against omicron and all other 'mutant strains' of covid-19\n\nhttps://t.co/t7zacadknp   
441671                                                                                                                    @realdailywire corrected-japan's kowa says ivermectin showed 'antiviral effect' against omicron in research\nhttps://t.co/gzevt8t9cz   
441672                                                                                                                                                        2 new omicron symptoms you won’t realize are from covid https://t.co/9yweo1kukg via @deseretnews   
441673                                                                  covid-19 omicron variant now dominant in italy, health body says - reuters\n\npublished at :2022-01-14t12:09:00z\nsource:"#reuters"\n\nhttps://t.co/srhwh9hclw https://t.co/qqspqpyml2   
441674  good grief . . . where’s the logic in this @shabirmadh @tuliodna . . . ‘south africans who test positive for the coronavirus but show no symptoms of covid-19 will no longer be required to self-isolate’ \n#covid omicron \n\nhttps://t.co/owhxpguqzz   

                                                                                                                                                                                           clean_text  \
441670                                                                                                      ivermectin has antiviral effect against omicron and all other mutant strains of covid19    

In [ ]:
df.isnull().sum()

created_at          2
id                  0
text               27
user_id            30
omicron_tweets     27
clean_text         76
compound          125
neg               125
neu               125
pos               125
week                0
UIN                 0
dtype: int64

In [ ]:
df = df.dropna()
print(df.shape)
df.isnull().sum()


(441547, 12)


created_at        0
id                0
text              0
user_id           0
omicron_tweets    0
clean_text        0
compound          0
neg               0
neu               0
pos               0
week              0
UIN               0
dtype: int64

In [ ]:
#df = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Vader Sentiment Output/V_Sentiment_Week1.csv", engine ='python')
# 1464292750883319813

In [ ]:
df.head(1000)

created_at                   id  \
0    Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1    Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2    Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3    Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4    Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   
5    Fri Nov 26 17:59:04 +0000 2021  1464292636521644045   
6    Fri Nov 26 17:59:13 +0000 2021  1464292675553742854   
7    Fri Nov 26 17:59:05 +0000 2021  1464292642808815622   
8    Fri Nov 26 17:58:46 +0000 2021  1464292561443512325   
9    Fri Nov 26 17:59:06 +0000 2021  1464292644507504645   
10   Fri Nov 26 17:58:58 +0000 2021  1464292612207263759   
11   Fri Nov 26 17:59:15 +0000 2021  1464292681413275653   
12   Fri Nov 26 17:59:28 +0000 2021  1464292736312516618   
13   Fri Nov 26 17:59:31 +0000 2021  1464292750883319813   
14   Fri Nov 26 17:59:32 +0000 2021  1464292753366528002   
15   Fri Nov 26 17:59:28 +0000 2021  1464292737570775041   
16   Fri Nov 26 17:59:21 +0000 2021  1464292710022623239   
17   Fri Nov 26 17:59:22 +0000 2021  1464292713688358914   
18   Fri Nov 26 17:59:43 +0000 2021  1464292799025668111   
19   Fri Nov 26 17:59:57 +0000 2021  1464292859557957635   
20   Fri Nov 26 17:59:58 +0000 2021  1464292865308303377   
21   Fri Nov 26 18:00:02 +0000 2021  1464292879556399112   
22   Fri Nov 26 18:00:01 +0000 2021  1464292876427444245   
23   Fri Nov 26 18:00:13 +0000 2021  1464292924347371521   
24   Fri Nov 26 18:00:35 +0000 2021  1464293020044443649   
25   Fri Nov 26 18:00:39 +0000 2021  1464293034531581953   
26   Fri Nov 26 18:00:39 +0000 2021  1464293037241036804   
27   Fri Nov 26 18:01:04 +0000 2021  1464293138596605955   
28   Fri Nov 26 18:01:07 +0000 2021  1464293153901629450   
29   Fri Nov 26 18:01:04 +0000 2021  1464293139259301890   
30   Fri Nov 26 18:01:30 +0000 2021  1464293251129786380   
31   Fri Nov 26 18:01:44 +0000 2021  1464293306293096451   
32   Fri Nov 26 18:01:43 +0000 2021  1464293303533375497   
33   Fri Nov 26 18:01:31 +0000 2021  1464293251721031683   
34   Fri Nov 26 18:01:33 +0000 2021  1464293262064291852   
35   Fri Nov 26 18:01:35 +0000 2021  1464293271337783301   
36   Fri Nov 26 18:01:49 +0000 2021  1464293329797988352   
37   Fri Nov 26 18:02:00 +0000 2021  1464293373800423428   
38   Fri Nov 26 18:02:22 +0000 2021  1464293468096897024   
39   Fri Nov 26 18:01:54 +0000 2021  1464293349167411202   
40   Fri Nov 26 18:02:56 +0000 2021  1464293608685809665   
41   Fri Nov 26 18:03:22 +0000 2021  1464293717322444809   
42   Fri Nov 26 18:03:12 +0000 2021  1464293676188770304   
43   Fri Nov 26 18:03:13 +0000 2021  1464293682857889794   
44   Fri Nov 26 18:03:27 +0000 2021  1464293741531959301   
45   Fri Nov 26 18:03:14 +0000 2021  1464293685143687173   
46   Fri Nov 26 18:03:10 +0000 2021  1464293667569549314   
47   Fri Nov 26 18:03:04 +0000 2021  1464293641699135496   
48   Fri Nov 26 18:03:33 +0000 2021  1464293763820445698   
49   Fri Nov 26 18:04:10 +0000 2021  1464293918325952513   
50   Fri Nov 26 18:04:09 +0000 2021  1464293916191207425   
51   Fri Nov 26 18:03:47 +0000 2021  1464293825648766983   
52   Fri Nov 26 18:03:57 +0000 2021  1464293863921577986   
53   Fri Nov 26 18:03:46 +0000 2021  1464293821005582344   
54   Fri Nov 26 18:04:33 +0000 2021  1464294017919688705   
55   Fri Nov 26 18:04:33 +0000 2021  1464294014660890630   
56   Fri Nov 26 18:04:13 +0000 2021  1464293933438095370   
57   Fri Nov 26 18:05:13 +0000 2021  1464294182823022599   
58   Fri Nov 26 18:05:26 +0000 2021  1464294238775087109   
59   Fri Nov 26 18:05:26 +0000 2021  1464294237437108227   
60   Fri Nov 26 18:05:31 +0000 2021  1464294259918393348   
61   Fri Nov 26 18:06:14 +0000 2021  1464294441892601862   
62   Fri Nov 26 18:05:56 +0000 2021  1464294365816258564   
63   Fri Nov 26 18:05:52 +0000 2021  1464294348863033347   
64   Fri Nov 26 18:06:03 +0000 2021  1464294393339432961   
65   Fri Nov 26 18:05:50 +0000 2021  1464294339971059717   
66   

In [ ]:
# suppressing the scientific notation for id number
#df['id'] = df['id'].apply(lambda x: '%.0f' % x)
#df['id'] = "{:.18f}". format(df['id'])
#type(df['id'][0])

In [ ]:
df.tail(1500)

created_at                   id  \
440175  Mon Jan 31 18:58:27 +0000 2022  1488225181948514307   
440176  Mon Jan 31 18:58:09 +0000 2022  1488225105838702592   
440177  Mon Jan 31 18:58:58 +0000 2022  1488225310873047040   
440178  Mon Jan 31 19:00:21 +0000 2022  1488225658614337536   
440179  Mon Jan 31 19:00:34 +0000 2022  1488225714289745926   
440180  Mon Jan 31 19:00:36 +0000 2022  1488225722988564480   
440181  Mon Jan 31 19:01:51 +0000 2022  1488226035565056009   
440182  Mon Jan 31 19:01:54 +0000 2022  1488226047208345607   
440183  Mon Jan 31 19:02:17 +0000 2022  1488226144168169475   
440184  Mon Jan 31 19:02:24 +0000 2022  1488226172336951296   
440185  Mon Jan 31 19:03:03 +0000 2022  1488226338209214464   
440186  Mon Jan 31 19:03:36 +0000 2022  1488226477619437568   
440187  Mon Jan 31 19:04:22 +0000 2022  1488226669399658499   
440188  Mon Jan 31 19:04:55 +0000 2022  1488226808378003459   
440189  Mon Jan 31 19:06:09 +0000 2022  1488227119238942720   
440190  Mon Jan 31 19:06:01 +0000 2022  1488227085013241858   
440191  Mon Jan 31 19:05:53 +0000 2022  1488227052843003906   
440192  Mon Jan 31 19:06:02 +0000 2022  1488227088930910209   
440193  Mon Jan 31 19:07:13 +0000 2022  1488227386810413059   
440194  Mon Jan 31 19:07:05 +0000 2022  1488227352668631046   
440195  Mon Jan 31 19:06:22 +0000 2022  1488227171789324289   
440196  Mon Jan 31 19:07:20 +0000 2022  1488227416241852418   
440197  Mon Jan 31 19:06:31 +0000 2022  1488227210465275904   
440198  Mon Jan 31 19:08:08 +0000 2022  1488227617274621953   
440199  Mon Jan 31 19:08:32 +0000 2022  1488227715874500609   
440200  Mon Jan 31 19:07:34 +0000 2022  1488227473435287556   
440201  Mon Jan 31 19:09:02 +0000 2022  1488227844798906370   
440202  Mon Jan 31 19:09:20 +0000 2022  1488227920728498179   
440203  Mon Jan 31 19:10:22 +0000 2022  1488228180259446784   
440204  Mon Jan 31 19:09:47 +0000 2022  1488228030837243906   
440205  Mon Jan 31 19:09:51 +0000 2022  1488228050961514496   
440206  Mon Jan 31 19:11:28 +0000 2022  1488228456416493568   
440207  Mon Jan 31 19:11:41 +0000 2022  1488228509633769472   
440208  Mon Jan 31 19:11:21 +0000 2022  1488228428411248641   
440209  Mon Jan 31 19:11:28 +0000 2022  1488228457280638980   
440210  Mon Jan 31 19:11:45 +0000 2022  1488228528323809284   
440211  Mon Jan 31 19:12:42 +0000 2022  1488228767541649409   
440212  Mon Jan 31 19:12:46 +0000 2022  1488228784511799304   
440213  Mon Jan 31 19:12:41 +0000 2022  1488228762865049606   
440214  Mon Jan 31 19:12:42 +0000 2022  1488228765708734476   
440215  Mon Jan 31 19:12:25 +0000 2022  1488228696859287552   
440216  Mon Jan 31 19:12:43 +0000 2022  1488228772155469834   
440217  Mon Jan 31 19:13:02 +0000 2022  1488228851822084099   
440218  Mon Jan 31 19:13:36 +0000 2022  1488228991353851904   
440219  Mon Jan 31 19:13:02 +0000 2022  1488228851675283457   
440220  Mon Jan 31 19:13:26 +0000 2022  1488228952686665728   
440221  Mon Jan 31 19:13:56 +0000 2022  1488229078771838976   
440222  Mon Jan 31 19:14:40 +0000 2022  1488229259395366912   
440223  Mon Jan 31 19:14:31 +0000 2022  1488229225438007305   
440224  Mon Jan 31 19:15:13 +0000 2022  1488229400277487619   
440225  Mon Jan 31 19:15:09 +0000 2022  1488229384586919937   
440226  Mon Jan 31 19:15:52 +0000 2022  1488229561766535169   
440227  Mon Jan 31 19:17:16 +0000 2022  1488229914893553664   
440228  Mon Jan 31 19:16:56 +0000 2022  1488229830118178817   
440229  Mon Jan 31 19:17:08 +0000 2022  1488229882358386698   
440230  Mon Jan 31 19:17:09 +0000 2022  1488229887257239552   
440231  Mon Jan 31 19:17:30 +0000 2022  1488229975799050247   
440232  Mon Jan 31 19:18:28 +0000 2022  1488230215918981121   
440233  Mon Jan 31 19:19:01 +0000 2022  1488230356645859329   
440234  Mon Jan 31 19:18:57 +0000 2022  1488230338392432642   
440235  Mon Jan 31 19:18:37 +0000 2022  1488230256385400835   
440236  Mon Jan 31 19:19:07 +0000 2022  1488230382004625408   
440237  Mon Jan 31 19:20:58 +0000 2022  1488230844904792065

In [ ]:
# Cleaning and lemmatization

nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')

STOP_WORDS = stopwords.words()

#remove_punc = "\"#$%&'()+,-./:;<=>?@[\]^_`{|}~"     # we kept ! and * because they are used by people to express sentiments


#df = df[['UIN', 'week', 'created_at', 'id', 'omicron_tweets', 'clean_text', 'compound', 'neg' , 'neu' ,'pos']]

print(df.shape)


EMOJI_PATTERN = re.compile("["
                          u"\U0001F600-\U0001F64F"  # emoticons
                          u"\U0001F300-\U0001F5FF"  # symbols & pictographs
                          u"\U0001F680-\U0001F6FF"  # transport & map symbols
                          u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
                          u"\U00002702-\U000027B0"
                          u"\U000024C2-\U0001F251"
                          "]+", flags=re.UNICODE)

def cleaning(text):
  '''
  Convert to lowercase.
  Rremove URL links, special characters and punctuation.
  Tokenize and remove stop words.
  '''
  text = text.lower()
  text = re.sub('https?://\S+|www\.\S+', '', text)
  text = re.sub('@[A-Za-z0-9]+', '', text)
  text = re.sub('<.*?>+', '', text)   # replacing HTML text with blank or whitespace
  
  #text_try = re.sub(r'[^\w\s]', '', text_try)
  #dtext = re.sub('[%s]' % re.escape(remove_punc), '', text)
  text = re.sub('\n', " ", text)
  text = re.sub('[%s]' % re.escape(string.punctuation), '', text)     
  # removes the puncutation characters. re.escape is used to escape the special characters that form puncuation characters. 
  #For eg, \" considers quote as character because of backslash
  text = re.sub('[’“”…]', '', text)
  
  text = text.encode("ascii", "ignore")     # consider only english alphanumeric characters
  text = text.decode()
  
  text = EMOJI_PATTERN.sub(r'', text)



  # removing the stop-words
  text_tokens = word_tokenize(text)
  tokens_without_sw = [
    word for word in text_tokens if not word in STOP_WORDS]
  filtered_sentence = (" ").join(tokens_without_sw)
  text = filtered_sentence

  return text

    
  
def lemmatizer(text_list):
  lmtzr = WordNetLemmatizer()
  lemm_tokens = [lmtzr.lemmatize(word) for word in text_list] #[lmtzr.lemmatize(word) for word in lst]
  lemmatized_text = (" ").join(lemm_tokens)
  text = lemmatized_text
  return text

# POS_TAGGER_FUNCTION : TYPE 1
def pos_tagger(nltk_tag):
  if nltk_tag.startswith('J'):
      return wordnet.ADJ
  elif nltk_tag.startswith('V'):
      return wordnet.VERB
  elif nltk_tag.startswith('N'):
      return wordnet.NOUN
  elif nltk_tag.startswith('R'):
      return wordnet.ADV
  else:         
      return None

def lemma3(clean_txt):
  pos_tagged = nltk.pos_tag(nltk.word_tokenize(clean_txt))
  wordnet_tagged = list(map(lambda x: (x[0], pos_tagger(x[1])), pos_tagged))

  lemmatized_sentence = []
  lmtzr = WordNetLemmatizer()
  for word, tag in wordnet_tagged:
    if tag is None:
    # if there is no available tag, append the token as is
      lemmatized_sentence.append(word)
    else:       
    # else use the tag to lemmatize the token
      lemmatized_sentence.append(lmtzr.lemmatize(word, tag))
  lemmatized_sentence = " ".join(lemmatized_sentence)
  return lemmatized_sentence

def remove_covid(lemm_text):
  lemm_text = re.sub('covid', '', lemm_text)
  lemm_text = re.sub('coronavirus', '', lemm_text)
  lemm_text = re.sub('corona', '', lemm_text)
  lemm_text = re.sub('variant', '', lemm_text)
  lemm_text = re.sub('omicron', '', lemm_text)
  return lemm_text


  



#if __name__ == "__main__":
#    max_rows = 1000  # 'None' to read whole file
    
df['clean_text'] = df['clean_text'].astype(str)
#df_reduced.head() 

#dt = df_reduced['name_plus_desp'].apply(cleaning)
df['clean_text2'] = df['clean_text'].apply(cleaning)



tt = TweetTokenizer()
df['tokenised_tweet'] = df['clean_text2'].apply(tt.tokenize)
#print(test)

df['lemmatized'] = df['tokenised_tweet'].apply(lemmatizer)

df['lemma_2'] = df['clean_text2'].apply(lemma3)


df.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/final_clean_tweets.csv", index=False)

df['lemma_3'] = df['lemma_2'].apply(remove_covid)

#func_lda(df['lemma_2'])

print("\n")

#num_topics,id2word,corpus,lda_model = func_lda(df['lemma_3'])


#dtm.shape # n_docs x m_words

#dtm
#df.head(900)



[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
(441547, 12)




In [ ]:
df.head()

created_at                   id  \
0  Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1  Fri Nov 26 16:11:42 +0000 2021  1464265614994952199   
2  Fri Nov 26 17:58:39 +0000 2021  1464292531970220036   
3  Fri Nov 26 17:58:37 +0000 2021  1464292524667854852   
4  Fri Nov 26 17:58:35 +0000 2021  1464292515901677570   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos    week  UIN  \
0    0.72

## Reading the stored cleaned tweet file

In [ ]:
#df.isnull().sum()
#df.shape

In [ ]:
df_cleanT = pd.read_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/final_clean_tweets.csv", engine= 'python')

In [ ]:
df_cleanT.columns

Index(['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos', 'week', 'UIN', 'clean_text2',
       'tokenised_tweet', 'lemmatized', 'lemma_2'],
      dtype='object')

In [ ]:

df_cleanT.tail()

created_at            id  \
441542  Tue Feb 01 05:02:03 +0000 2022  1.488377e+18   
441543  Tue Feb 01 05:02:09 +0000 2022  1.488377e+18   
441544  Tue Feb 01 05:03:18 +0000 2022  1.488377e+18   
441545  Tue Feb 01 05:02:19 +0000 2022  1.488377e+18   
441546  Tue Feb 01 05:04:44 +0000 2022  1.488378e+18   

                                                                                                                                                                                                                                                           text  \
441542                                                                                                                                  Ivermectin Has 'Antiviral Effect' Against Omicron And All Other 'Mutant Strains' Of Covid-19\n\nhttps://t.co/t7zACadkNP   
441543                                                                                                                     @realDailyWire CORRECTED-Japan's Kowa says ivermectin showed 'antiviral effect' against Omicron in research\nhttps://t.co/gZeVT8t9CZ   
441544                                                                                                                                                         2 new omicron symptoms you won’t realize are from COVID https://t.co/9yweO1KuKG via @DeseretNews   
441545                                                                   COVID-19 Omicron variant now dominant in Italy, health body says - Reuters\n\nPublished At :2022-01-14T12:09:00Z\nSource:"#Reuters"\n\nhttps://t.co/srhWh9hcLW https://t.co/QqSpqPYMl2   
441546  Good grief . . . Where’s the logic in this @ShabirMadh @Tuliodna . . . ‘South Africans who test positive for the coronavirus but show no symptoms of Covid-19 will no longer be required to self-isolate’ \n#covid #Omicron \n\nhttps://t.co/OwHxpGuQZz   

             user_id  \
441542  9.821061e+17   
441543  2.855330e+09   
441544  1.521389e+08   
441545  1.441500e+18   
441546  1.218511e+08   

                                                                                                                                                                                                                                                omicron_tweets  \
441542                                                                                                                                 ivermectin has 'antiviral effect' against omicron and all other 'mutant strains' of covid-19\n\nhttps://t.co/t7zacadknp   
441543                                                                                                                    @realdailywire corrected-japan's kowa says ivermectin showed 'antiviral effect' against omicron in research\nhttps://t.co/gzevt8t9cz   
441544                                                                                                                                                        2 new omicron symptoms you won’t realize are from covid https://t.co/9yweo1kukg via @deseretnews   
441545                                                                  covid-19 omicron variant now dominant in italy, health body says - reuters\n\npublished at :2022-01-14t12:09:00z\nsource:"#reuters"\n\nhttps://t.co/srhwh9hclw https://t.co/qqspqpyml2   
441546  good grief . . . where’s the logic in this @shabirmadh @tuliodna . . . ‘south africans who test positive for the coronavirus but show no symptoms of covid-19 will no longer be required to self-isolate’ \n#covid omicron \n\nhttps://t.co/owhxpguqzz   

                                                                                                                                                                                           clean_text  \
441542                                                                                                      ivermectin has antiviral effect against omicron and all other mutant strains of covid19     
441543                                  

In [ ]:
print(df_cleanT.shape)
df_cleanT.isnull().sum()

(441547, 16)


created_at         0
id                 0
text               0
user_id            0
omicron_tweets     0
clean_text         0
compound           0
neg                0
neu                0
pos                0
week               0
UIN                0
clean_text2        1
tokenised_tweet    0
lemmatized         1
lemma_2            1
dtype: int64

In [ ]:
df_cleanT[df_cleanT.isnull().any(axis=1)]

created_at            id  \
255966  Mon Dec 27 21:05:00 +0000 2021  1.475573e+18   

                                                                                                         text  \
255966  Thosehttps://www.deseret.com/coronavirus/2021/12/27/22855385/omicron-variant-more-contagious-dr-fauci   

            user_id  \
255966  478295779.0   

                                                                                               omicron_tweets  \
255966  thosehttps://www.deseret.com/coronavirus/2021/12/27/22855385/omicron-variant-more-contagious-dr-fauci   

       clean_text  compound  neg  neu  pos    week     UIN clean_text2  \
255966      those       0.0  0.0  1.0  0.0  week_6  256053         NaN   

       tokenised_tweet lemmatized lemma_2  
255966              []        NaN     NaN

In [ ]:
df_cleanT = df_cleanT.dropna()

In [ ]:
df_cleanT.isnull().sum()

created_at         0
id                 0
text               0
user_id            0
omicron_tweets     0
clean_text         0
compound           0
neg                0
neu                0
pos                0
week               0
UIN                0
clean_text2        0
tokenised_tweet    0
lemmatized         0
lemma_2            0
dtype: int64

In [ ]:
df_cleanT.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/final_clean_tweets2.csv", index=False)

In [ ]:
df_cleanT.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 441546 entries, 0 to 441546
Data columns (total 16 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   created_at       441546 non-null  object 
 1   id               441546 non-null  float64
 2   text             441546 non-null  object 
 3   user_id          441546 non-null  float64
 4   omicron_tweets   441546 non-null  object 
 5   clean_text       441546 non-null  object 
 6   compound         441546 non-null  float64
 7   neg              441546 non-null  float64
 8   neu              441546 non-null  float64
 9   pos              441546 non-null  float64
 10  week             441546 non-null  object 
 11  UIN              441546 non-null  int64  
 12  clean_text2      441546 non-null  object 
 13  tokenised_tweet  441546 non-null  object 
 14  lemmatized       441546 non-null  object 
 15  lemma_2          441546 non-null  object 
dtypes: float64(6), int64(1), object(9)
mem

In [ ]:
df_cleanT['id'] = df_cleanT['id'].astype(str)

In [ ]:
df_cleanT.head()

created_at                      id  \
0  Sun Nov 21 05:38:11 +0000 2021   1.462294248007504e+18   
1  Fri Nov 26 16:11:42 +0000 2021   1.464265614994952e+18   
2  Fri Nov 26 17:58:39 +0000 2021    1.46429253197022e+18   
3  Fri Nov 26 17:58:37 +0000 2021  1.4642925246678548e+18   
4  Fri Nov 26 17:58:35 +0000 2021  1.4642925159016776e+18   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos    week

## LDA implementation

In [ ]:
!pip install pyLDAvis==3.2.2
# !pip install pickle
!pip install gensim

     |████████████████████████████████| 1.7 MB 5.6 MB/s 
  Created wheel for pyLDAvis: filename=pyLDAvis-3.2.2-py2.py3-none-any.whl size=135617 sha256=0df4d37f14a921a045c5a376c0c15db5b29f473570a42b0977389ca010448757
  Stored in directory: /root/.cache/pip/wheels/f8/b1/9b/560ac1931796b7303f7b517b949d2d31a4fbc512aad3b9f284
Successfully built pyLDAvis


In [ ]:

'''
import pyLDAvis.gensim
# import pyLDAvis.gensim as gensimvis
import pickle 
import pyLDAvis

# Visualize the topics
pyLDAvis.enable_notebook()
LDAvis_data_filepath = os.path.join('/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+str(num_topics))

# # this is a bit time consuming - make the if statement True
# # if you want to execute visualization prep yourself
if 1 == 1:
    LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)
    with open(LDAvis_data_filepath, 'wb') as f:
        pickle.dump(LDAvis_prepared, f)

# load the pre-prepared pyLDAvis data from disk
with open(LDAvis_data_filepath, 'rb') as f:
    LDAvis_prepared = pickle.load(f)
pyLDAvis.save_html(LDAvis_prepared, '/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+ str(num_topics) +'.html')
LDAvis_prepared
'''

"\nimport pyLDAvis.gensim\n# import pyLDAvis.gensim as gensimvis\nimport pickle \nimport pyLDAvis\n\n# Visualize the topics\npyLDAvis.enable_notebook()\nLDAvis_data_filepath = os.path.join('/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+str(num_topics))\n\n# # this is a bit time consuming - make the if statement True\n# # if you want to execute visualization prep yourself\nif 1 == 1:\n    LDAvis_prepared = pyLDAvis.gensim.prepare(lda_model, corpus, id2word)\n    with open(LDAvis_data_filepath, 'wb') as f:\n        pickle.dump(LDAvis_prepared, f)\n\n# load the pre-prepared pyLDAvis data from disk\nwith open(LDAvis_data_filepath, 'rb') as f:\n    LDAvis_prepared = pickle.load(f)\npyLDAvis.save_html(LDAvis_prepared, '/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/lda_results/ldavis_prepared_'+ str(num_topics) +'.html')\nLDAvis_prepared\n"

## Unsupervised CoRex result

In [ ]:
# Unsupervised CoRex
print("\n")

corex_func(df_cleanT)

print("\n")



/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


['00', '000', '0000', '00001', '000026', '00003', '0000omicron', '0001', '00022', '0002eth', '0003', '0004', '0005', '0006', '000am', '000s', '001', '0015', '002', '0024', '0025', '0028', '003', '0033utc', '004', '005', '00501', '0058', '006', '0065', '007', '0077', '0078', '008', '009', '0096', '00mdjc', '01', '010', '0100', '0100am', '0101', '01012022', '010122', '0102', '01022022', '01032022', '0105', '01052022', '01062022', '0107', '01072022', '0108', '01082022', '0109', '01092022', '011', '01102022', '011022', '01112021', '01112022', '0112', '01122021', '011221', '011422', '01152022', '011522', '011722', '011822', '01192022', '011922', '012', '012022', '0121', '012122', '0122', '01222022', '012222', '012522', '012622', '012722', '012922', '013', '013122', '0138pm', '014', '014y', '015', '0156', '016', '017', '017yearolds', '018', '019', '01908', '01the', '02', '020', '02012022', '020122', '021', '02122021', '022', '0230', '024', '025', '026', '027', '028', '029', '02dec2021', '03'

## Semi-Supervised CoRex results

Correlation Explanation (CorEx) is a topic model that yields rich topics that are maximally 
informative about a set of documents. 
It classifies the text into topics.

Each topic explains a certain portion of the total correlation (TC). 
We can access the topic TCs through the tcs attribute, as well as the overall TC .

CorEx instead estimates the probability a document belongs to a topic given that document's words. 
As a result, the probabilities across topics for a given document do not have to add up to 1. 
The estimated probabilities of topics for each document can be accessed through 
log_p_y_given_x or p_y_given_x.






In [ ]:
#df.isnull().sum()

In [ ]:
df_cleanT.isnull().sum()

created_at         0
id                 0
text               0
user_id            0
omicron_tweets     0
clean_text         0
compound           0
neg                0
neu                0
pos                0
week               0
UIN                0
clean_text2        0
tokenised_tweet    0
lemmatized         0
lemma_2            0
dtype: int64

In [ ]:
df_cleanT.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 441546 entries, 0 to 441546
Data columns (total 16 columns):
 #   Column           Non-Null Count   Dtype  
---  ------           --------------   -----  
 0   created_at       441546 non-null  object 
 1   id               441546 non-null  object 
 2   text             441546 non-null  object 
 3   user_id          441546 non-null  float64
 4   omicron_tweets   441546 non-null  object 
 5   clean_text       441546 non-null  object 
 6   compound         441546 non-null  float64
 7   neg              441546 non-null  float64
 8   neu              441546 non-null  float64
 9   pos              441546 non-null  float64
 10  week             441546 non-null  object 
 11  UIN              441546 non-null  int64  
 12  clean_text2      441546 non-null  object 
 13  tokenised_tweet  441546 non-null  object 
 14  lemmatized       441546 non-null  object 
 15  lemma_2          441546 non-null  object 
dtypes: float64(5), int64(1), object(10)
me

In [ ]:
#df_cleanT = df_cleanT.dropna()

In [ ]:
df_cleanT.head()

created_at                      id  \
0  Sun Nov 21 05:38:11 +0000 2021   1.462294248007504e+18   
1  Fri Nov 26 16:11:42 +0000 2021   1.464265614994952e+18   
2  Fri Nov 26 17:58:39 +0000 2021    1.46429253197022e+18   
3  Fri Nov 26 17:58:37 +0000 2021  1.4642925246678548e+18   
4  Fri Nov 26 17:58:35 +0000 2021  1.4642925159016776e+18   

                                                                                                                                                                                                                 text  \
0  It was so nice to join @UBCAOII for initiation - the first in person one the chapter has held since the world closed down because of #COVID19 @alphaomicronpi @aoiivancouver @AOII_Calgary https://t.co/3ApQZofbHM   
1                                                                                                New Nu Novel Coronavirus SARS-CoV2 COVID-19 variant.\n\nCouldn’t be easy like Kappa or Lambda or Omicron or even Pi.   
2                                                                                                                                              PUT AWAY THE "Nu" jokes - the name is Omicron. https://t.co/CgsZlzK4Cw   
3                                                                                                             @RiochtConor2 BREAKING: WHO designates new coronavirus strain as a variant of concern, names it Omicron   
4                                                                                                                                                                                     Omicron https://t.co/m2vLDtse5L   

        user_id  \
0  1.634359e+07   
1  1.754451e+07   
2  4.321370e+07   
3  2.719413e+07   
4  1.336693e+18   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos    week

In [ ]:
df_cleanT.tail()

created_at                      id  \
441542  Tue Feb 01 05:02:03 +0000 2022   1.488377083076264e+18   
441543  Tue Feb 01 05:02:09 +0000 2022  1.4883771069920335e+18   
441544  Tue Feb 01 05:03:18 +0000 2022  1.4883773968058368e+18   
441545  Tue Feb 01 05:02:19 +0000 2022  1.4883771493084815e+18   
441546  Tue Feb 01 05:04:44 +0000 2022  1.4883777565262067e+18   

                                                                                                                                                                                                                                                           text  \
441542                                                                                                                                  Ivermectin Has 'Antiviral Effect' Against Omicron And All Other 'Mutant Strains' Of Covid-19\n\nhttps://t.co/t7zACadkNP   
441543                                                                                                                     @realDailyWire CORRECTED-Japan's Kowa says ivermectin showed 'antiviral effect' against Omicron in research\nhttps://t.co/gZeVT8t9CZ   
441544                                                                                                                                                         2 new omicron symptoms you won’t realize are from COVID https://t.co/9yweO1KuKG via @DeseretNews   
441545                                                                   COVID-19 Omicron variant now dominant in Italy, health body says - Reuters\n\nPublished At :2022-01-14T12:09:00Z\nSource:"#Reuters"\n\nhttps://t.co/srhWh9hcLW https://t.co/QqSpqPYMl2   
441546  Good grief . . . Where’s the logic in this @ShabirMadh @Tuliodna . . . ‘South Africans who test positive for the coronavirus but show no symptoms of Covid-19 will no longer be required to self-isolate’ \n#covid #Omicron \n\nhttps://t.co/OwHxpGuQZz   

             user_id  \
441542  9.821061e+17   
441543  2.855330e+09   
441544  1.521389e+08   
441545  1.441500e+18   
441546  1.218511e+08   

                                                                                                                                                                                                                                                omicron_tweets  \
441542                                                                                                                                 ivermectin has 'antiviral effect' against omicron and all other 'mutant strains' of covid-19\n\nhttps://t.co/t7zacadknp   
441543                                                                                                                    @realdailywire corrected-japan's kowa says ivermectin showed 'antiviral effect' against omicron in research\nhttps://t.co/gzevt8t9cz   
441544                                                                                                                                                        2 new omicron symptoms you won’t realize are from covid https://t.co/9yweo1kukg via @deseretnews   
441545                                                                  covid-19 omicron variant now dominant in italy, health body says - reuters\n\npublished at :2022-01-14t12:09:00z\nsource:"#reuters"\n\nhttps://t.co/srhwh9hclw https://t.co/qqspqpyml2   
441546  good grief . . . where’s the logic in this @shabirmadh @tuliodna . . . ‘south africans who test positive for the coronavirus but show no symptoms of covid-19 will no longer be required to self-isolate’ \n#covid omicron \n\nhttps://t.co/owhxpguqzz   

                                                                                                                                                                                           clean_text  \
441542                                                                                                      ivermectin has antiviral effect against omicron and all other mutant stra

In [ ]:
len(df_cleanT['id'])

441546

In [ ]:
all_topics =  ['symptoms','prevention', 'testing', 'treatment', 'economic_impact', 'travel', 'vaccination', 'vaccination_opposition', 
 'policies', 'causes', 'transmission', 'children_education', 'government', 'mental_health']


tab, words = corex_func_anchor(df_cleanT)



<class 'scipy.sparse.csr.csr_matrix'>
(441546, 64344) 



/usr/local/lib/python3.7/dist-packages/sklearn/utils/deprecation.py:87: FutureWarning: Function get_feature_names is deprecated; get_feature_names is deprecated in 1.0 and will be removed in 1.2. Please use get_feature_names_out instead.
  warnings.warn(msg, category=FutureWarning)


(441546, 59508)


THESE ARE THE ANCHORS
[['cold', 'cough', 'flu', 'fever', 'headache', 'sore', 'muscle', 'breath', 'lungs', 'nausea', 'vomit', 'diarrhea', 'fever', 'fatigue', 'tired', 'symptom', 'mild', 'disease', 'reinfection', 'illness'], ['mask', 'sanitizer', 'distance', 'glove', 'ppe', 'kit', 'n95', 'quarantine', 'wash', 'isolation', 'wearamask', 'maskup', 'kn95'], ['test', 'positive', 'negative', 'oximeter', 'pcr', 'rtpcr', 'detect', 'report'], ['antibody', 'sotrovimab', 'therapy', 'antigen', 'bamlanivimab', 'etesevimab', 'casirivimab', 'imdevimab', 'sotrovimab', 'tixagevimab', 'cilgavimab', 'evusheld', 'medication', 'ibuprofen', 'pharmacy', 'capsule', 'tablet', 'ayurveda', 'ivermectin', 'pill', 'injection', 'doctor', 'mrna', 'monoclonal', 'icu'], ['economic', 'stock', 'market', 'layoff', 'unemployed', 'job', 'interview', 'poor', 'wage', 'salary', 'finance', 'closure', 'price', 'investor', 'crypto', 'bitcoin', 'inflation'], ['travel', 'flight', 'cab', 'train', 'bus', 'metro', 'pub

In [ ]:
df_result = pd.DataFrame(tab, columns = all_topics, index=df_cleanT.index)
df_result = round(df_result, 6)
df_result.head(1000)

#df_cor = corex_func_anchor(df)
#df_cor

symptoms  prevention    testing  treatment  economic_impact     travel  \
0   -19.219665  -19.405829 -18.352865 -16.583070       -18.016643 -17.527316   
1   -19.215943  -19.406415 -21.541073 -15.302919       -18.026078 -17.500745   
2   -18.677930  -19.405419 -18.387847 -16.582746       -18.015226 -17.496779   
3   -17.933863  -19.405448 -18.336563 -16.583125       -16.818010 -17.469641   
4   -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   
5   -18.677930  -19.405421 -18.387847 -16.582736       -18.015247 -17.496779   
6   -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   
7   -18.677941  -19.405346 -18.387847 -16.582962       -18.014199 -17.496779   
8   -18.677929  -19.405213 -18.387847 -16.582479       -18.951742 -17.496746   
9   -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   
10  -18.677930  -19.401542 -18.387847 -15.313025       -18.015392 -17.496828   
11    0.000000  -19.405573 -18.383355 -16.545330       -16.820443 -14.491321   
12  -18.677940  -19.405436 -18.387853 -16.595213       -18.036705 -17.496860   
13  -19.219655  -19.405403 -18.387840 -16.582519       -16.831731 -17.488620   
14  -14.601352  -19.405689 -18.387875 -16.668162       -18.024263 -17.415712   
15  -17.933909  -19.405448 -18.336563 -16.582951       -16.818018 -17.488330   
16  -17.320352  -19.405494 -17.168304 -16.583119       -18.019053 -17.457740   
17  -19.219644  -19.405405 -18.387894 -15.253198       -18.016046 -17.496792   
18  -18.677956  -17.131394 -18.389112 -16.583149       -18.010131 -17.496719   
19  -18.678150  -19.405338 -18.387847 -16.582943       -17.884790 -17.496837   
20  -17.320347  -19.405516 -17.168297 -16.574153       -16.821795 -17.449274   
21  -18.677934  -19.405442 -24.690953 -16.583050       -16.818020 -17.488322   
22  -19.219649  -19.405410 -18.387847 -16.582846       -18.015511 -17.496805   
23  -19.219645  -19.405410 -18.387847 -16.582731       -18.015094 -17.496779   
24  -18.678119  -19.405878 -18.388014 -15.370571       -17.998423 -17.499094   
25  -18.677931  -19.405458 -18.336570 -16.583169       -18.017881 -17.497038   
26  -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   
27  -15.583622  -19.408807 -16.157757 -16.588413       -16.806223 -15.897340   
28  -18.677914  -18.284038 -18.387839 -16.585872       -18.017142 -17.496760   
29  -17.933905  -19.405251 -18.336569 -16.582181       -18.014054 -17.496740   
30    0.000000  -19.405573 -18.383355 -16.545330       -16.820443 -14.491321   
31    0.000000  -19.405573 -18.383355 -16.545330       -16.820443 -14.491321   
32  -18.677942  -19.405537 -18.387889 -16.583909       -18.017499 -17.500513   
33  -18.677934  -19.405426 -18.387839 -16.582826       -18.015425 -17.496708   
34  -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   
35  -18.678140  -19.405421 -18.387847 -16.582738       -17.885470 -17.496779   
36  -18.677928  -19.405382 -18.387847 -16.583052       -18.018152 -17.497121   
37  -17.116862  -19.405422 -18.336563 -16.583051       -16.817987 -17.488377   
38  -18.402597  -19.405455 -18.336563 -16.583367       -17.966393 -17.496886   
39  -17.320375  -19.405812 -17.168297 -16.573226        -1.108124 -17.429549   
40  -16.966176  -19.405789 -18.387847 -16.668593       -18.026013 -17.495431   
41  -18.677953  -19.405442 -18.387853 -16.601598       -18.048835 -17.496939   
42  -19.219670  -19.405481 -16.989758 -16.584498       -18.013348   0.000000   
43  -17.933909  -19.405448 -18.336563 -16.582951       -16.818018 -17.488330   
44  -17.320348  -16.583740 -16.334024 -16.574747         0.000000 -17.450618   
45  -16.917919  -19.405472 -18.387847 -16.584676       -18.043101 -17.497007   
46  -18.677922  -19.405378 -18.387840 -15.477449       -12.189519 -17.498854   
47  -18.677928  -19.405474 -18.387847 -16.584200       -18.015630 -17.496804   
48  -18.677972  -19.405659 -18.387876 -16.586328       -18.012922 -17.497329   
49  -1

In [ ]:
df_result.tail(100)

symptoms  prevention    testing  treatment  economic_impact  \
441447 -19.219646  -19.405450 -18.387847 -16.583242       -18.018229   
441448 -15.641967  -19.402934 -18.387839 -16.582648       -18.016320   
441449 -19.219630  -19.404911 -18.388518 -15.049368       -14.457895   
441450 -19.219646  -19.405450 -18.387847 -16.583242       -18.018229   
441451 -18.677925  -17.774433 -18.387818   0.000000       -18.018540   
441452 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441453 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441454 -17.560359  -19.404970 -20.038926 -16.583580       -14.807718   
441455 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441456 -19.219643  -19.405419 -18.387847 -16.581599       -15.352952   
441457 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441458 -19.219634  -19.405707 -18.387840   0.000000       -18.013676   
441459 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441460 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441461 -16.397263  -19.403969 -16.745121 -16.582762       -18.018647   
441462 -19.219646  -19.405450 -18.387847 -16.583242       -18.018229   
441463 -18.677943  -19.405368 -18.387847 -16.585290         0.000000   
441464 -19.219646  -19.405450 -18.387847 -16.583242       -18.018229   
441465 -19.229756  -19.405647 -16.773671 -16.578806       -18.016630   
441466 -19.214392  -19.323855 -15.713771   0.000000       -18.023497   
441467 -18.677918  -19.405466 -18.387847   0.000000       -18.014865   
441468 -18.677943  -19.405368 -18.387847 -16.585299         0.000000   
441469 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441470 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441471 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441472 -19.219647  -19.405567 -18.387839   0.000000       -18.015984   
441473 -18.677163  -17.632522   0.000000  -0.172313       -18.016829   
441474 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441475 -18.109795  -19.405479 -18.387847 -16.573298       -18.015117   
441476 -15.085469  -19.341126 -18.387847   0.000000       -18.015324   
441477 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441478   0.000000  -19.405417 -18.387847 -16.575463       -18.014646   
441479 -19.219647  -19.405467 -18.387847 -16.583864       -18.019861   
441480 -18.677917  -19.405471 -18.387847   0.000000       -18.015337   
441481 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441482 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441483 -19.219646  -19.388883 -18.387847 -16.596321       -18.020278   
441484 -19.219647  -19.405467 -18.387847 -16.583864       -18.019861   
441485 -18.677917  -19.405471 -18.387847   0.000000       -18.015337   
441486 -18.677917  -19.405471 -18.387847   0.000000       -18.015337   
441487 -19.485164  -19.402916 -18.387914 -16.578433       -18.034899   
441488 -19.219646  -19.405453 -18.387847 -16.583597       -18.019588   
441489 -19.219647  -19.405575 -18.387839   0.000000       -18.015926   
441490 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441491 -18.688026  -19.405473 -17.607945   0.000000       -18.015547   
441492 -13.425901  -19.406528 -18.387839 -16.582592       -16.705471   
441493 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441494 -19.219646  -19.405453 -18.387847 -16.583597       -18.019588   
441495 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441496 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441497 -19.219651  -19.405483 -18.387847 -16.583808       -18.019854   
441498 -18.475604  -19.405672 -18.388033   0.000000       -18.014481   
441499 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441500 -19.219651  -19.405483 -18.387847 -16.583808       -18.019854   
441501 -16.607173  -19.391897 -18.387847 -16.5825

In [ ]:
df_cleanT['UIN'].head()

0    1
1    2
2    3
3    4
4    5
Name: UIN, dtype: int64

In [ ]:
df_result.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 441546 entries, 0 to 441546
Data columns (total 14 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   symptoms                441546 non-null  float64
 1   prevention              441546 non-null  float64
 2   testing                 441546 non-null  float64
 3   treatment               441546 non-null  float64
 4   economic_impact         441546 non-null  float64
 5   travel                  441546 non-null  float64
 6   vaccination             441546 non-null  float64
 7   vaccination_opposition  441546 non-null  float64
 8   policies                441546 non-null  float64
 9   causes                  441546 non-null  float64
 10  transmission            441546 non-null  float64
 11  children_education      441546 non-null  float64
 12  government              441546 non-null  float64
 13  mental_health           441546 non-null  float64
dtypes: float64(14)
memor

In [ ]:

#df_result['week'] = df_cleanT['week']

In [ ]:
#df_result['UIN'] = df_cleanT['UIN'].astype(int)

In [ ]:
#df_final_result = pd.concat([df_result, df_cleanT[['UIN', 'week', 'id']]], axis =1)

In [ ]:
#df_sample2 = df_result.iloc[0:1500]
max_ValueInd = df_result.idxmax(axis=1)
df_result['Tweet_topic'] = max_ValueInd
df_result.head(1000)
df_result['Tweet_topic'].value_counts()

mental_health             106600
transmission               81330
vaccination                52772
testing                    49143
symptoms                   37989
prevention                 24100
travel                     16491
policies                   16072
treatment                  14435
economic_impact            11994
government                  9898
causes                      8219
vaccination_opposition      6771
children_education          5732
Name: Tweet_topic, dtype: int64

In [ ]:
df_result.head()

symptoms  prevention    testing  treatment  economic_impact     travel  \
0 -19.219665  -19.405829 -18.352865 -16.583070       -18.016643 -17.527316   
1 -19.215943  -19.406415 -21.541073 -15.302919       -18.026078 -17.500745   
2 -18.677930  -19.405419 -18.387847 -16.582746       -18.015226 -17.496779   
3 -17.933863  -19.405448 -18.336563 -16.583125       -16.818010 -17.469641   
4 -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   

   vaccination  vaccination_opposition   policies     causes  transmission  \
0   -19.547332              -16.545229 -15.621195 -13.772417    -28.169512   
1   -21.116119              -16.620419 -16.383243 -15.230658    -21.062278   
2   -21.116119              -16.567236 -15.620894 -13.492981    -18.675337   
3   -21.118538              -16.576895 -15.620891 -15.096107    -19.244500   
4   -21.116119              -16.567328 -15.620894 -15.100422    -18.675322   

   children_education  government  mental_health    Tweet_topic  
0          -18.814993  -15.527509      -6.028125  mental_health  
1          -20.749207  -15.545786      -7.749233  mental_health  
2          -20.613957  -15.545756      -6.854449  mental_health  
3          -20.620848  -15.135189     -10.086894  mental_health  
4          -20.613949  -15.545756      -8.601082  mental_health

In [ ]:
df_result.shape

(441546, 15)

In [ ]:
df_cleanT.shape

(441546, 16)

In [ ]:
df_cleanT.columns

Index(['created_at', 'id', 'text', 'user_id', 'omicron_tweets', 'clean_text',
       'compound', 'neg', 'neu', 'pos', 'week', 'UIN', 'clean_text2',
       'tokenised_tweet', 'lemmatized', 'lemma_2'],
      dtype='object')

In [ ]:
df_result.columns

Index(['symptoms', 'prevention', 'testing', 'treatment', 'economic_impact',
       'travel', 'vaccination', 'vaccination_opposition', 'policies', 'causes',
       'transmission', 'children_education', 'government', 'mental_health',
       'Tweet_topic'],
      dtype='object')

In [ ]:
df_final_result = pd.concat([df_result, df_cleanT[['UIN', 'week', 'id','clean_text', 'user_id', 'compound', 'lemma_2']]], axis =1)



In [ ]:
df_final_result['Sentiment_Class']=''
df_final_result.loc[df_final_result.compound >= 0.05,'Sentiment_Class']='Positive'
df_final_result.loc[(df_final_result.compound< 0.05) & (df_final_result.compound > -0.05),'Sentiment_Class']='Neutral'
df_final_result.loc[df_final_result.compound <= -0.05,'Sentiment_Class']='Negative'

In [ ]:
df_final_result = df_final_result[['id', 'UIN', 'week', 'user_id', 'clean_text', 'compound', 'lemma_2', 'symptoms', 'prevention', 'testing', 'treatment', 'economic_impact',
       'travel', 'vaccination', 'vaccination_opposition', 'policies', 'causes',
       'transmission', 'children_education', 'government', 
       'mental_health', 'Tweet_topic', 'Sentiment_Class']]

In [ ]:
df_final_result.tail()

id     UIN     week       user_id  \
441542   1.488377083076264e+18  441671  week_11  9.821061e+17   
441543  1.4883771069920335e+18  441672  week_11  2.855330e+09   
441544  1.4883773968058368e+18  441673  week_11  1.521389e+08   
441545  1.4883771493084815e+18  441674  week_11  1.441500e+18   
441546  1.4883777565262067e+18  441675  week_11  1.218511e+08   

                                                                                                                                                                                           clean_text  \
441542                                                                                                      ivermectin has antiviral effect against omicron and all other mutant strains of covid19     
441543                                                                                                      correctedjapans kowa says ivermectin showed antiviral effect against omicron in research    
441544                                                                                                                                   2 new omicron symptoms you wont realize are from covid  via    
441545                                                                        covid19 omicron variant now dominant in italy health body says  reuters  published at 20220114t120900z sourcereuters      
441546  good grief    wheres the logic in this      ‘south africans who test positive for the coronavirus but show no symptoms of covid19 will no longer be required to selfisolate  covid omicron      

        compound  \
441542   -0.2960   
441543    0.0000   
441544    0.0000   
441545    0.0000   
441546   -0.5346   

                                                                                                                                lemma_2  \
441542                                                                        ivermectin antiviral effect omicron mutant strain covid19   
441543                                                       correctedjapans kowa say ivermectin show antiviral effect omicron research   
441544                                                                                     2 new omicron symptom wont realize covid via   
441545                            covid19 omicron variant dominant italy health body say reuters publish 20220114t120900z sourcereuters   
441546  good grief wheres logic south african test positive coronavirus show symptoms covid19 longer required selfisolate covid omicron   

         symptoms  prevention    testing  treatment  economic_impact  \
441542 -18.475564  -19.405458 -18.387847   0.000000       -18.014653   
441543 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441544   0.000000  -19.405458 -18.336570 -16.583170       -18.017835   
441545 -18.108379  -19.405545 -18.566656 -15.365728       -18.021048   
441546 -14.306460  -16.838903   0.000000 -16.603530       -18.042752   

           travel  vaccination  vaccination_opposition   policies     causes  \
441542 -17.496732   -21.116118              -16.564844 -15.620743 -15.110073   
441543 -17.497598   -20.509502              -16.568931 -15.620800 -15.115348   
441544 -17.497039   -20.306017              -16.566825 -15.620912 -15.107265   
441545 -17.497012   -22.345796              -16.583566 -15.621015 -15.129535   
441546 -17.430494   -20.529619              -16.591428 -15.587561 -15.109626   

        transmission  children_education  government  mental_health  \
441542    -18.074191          -20.614231  -15.545773      -8.584191   
441543    -18.675322          -20.600556  -15.532207      -8.600619   
441544    -16.954375          -20.614312  -15.545759      -6.693618   
441545    -23.866427          -20.615722  -15.529129     -11.477830   
441546    -17.394985          -20.615068  -15.545308      -4.193139   

          Tweet_topic Sentiment_Class  
441542      treatment        Negative  
441543      treatment         Neutral  
441544       

In [ ]:
df_final_result.head()

id  UIN    week       user_id  \
0   1.462294248007504e+18    1  week_1  1.634359e+07   
1   1.464265614994952e+18    2  week_1  1.754451e+07   
2    1.46429253197022e+18    3  week_1  4.321370e+07   
3  1.4642925246678548e+18    4  week_1  2.719413e+07   
4  1.4642925159016776e+18    5  week_1  1.336693e+18   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                   new nu novel coronavirus sarscov2 covid19 variant  couldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound  \
0    0.7253   
1   -0.2996   
2    0.2500   
3   -0.0516   
4    0.0000   

                                                                                         lemma_2  \
0               nice join initiation first person chapter hold since world close covid19 calgary   
1  new novel coronavirus sarscov2 covid19 variant couldnt easy like kappa lambda omicron even pi   
2                                                                          put away joke omicron   
3                            break designate new coronavirus strain variant concern name omicron   
4                                                                                        omicron   

    symptoms  prevention    testing  treatment  economic_impact     travel  \
0 -19.219665  -19.405829 -18.352865 -16.583070       -18.016643 -17.527316   
1 -19.215943  -19.406415 -21.541073 -15.302919       -18.026078 -17.500745   
2 -18.677930  -19.405419 -18.387847 -16.582746       -18.015226 -17.496779   
3 -17.933863  -19.405448 -18.336563 -16.583125       -16.818010 -17.469641   
4 -18.677930  -19.405421 -18.387847 -16.582736       -18.015246 -17.496779   

   vaccination  vaccination_opposition   policies     causes  transmission  \
0   -19.547332              -16.545229 -15.621195 -13.772417    -28.169512   
1   -21.116119              -16.620419 -16.383243 -15.230658    -21.062278   
2   -21.116119              -16.567236 -15.620894 -13.492981    -18.675337   
3   -21.118538              -16.576895 -15.620891 -15.096107    -19.244500   
4   -21.116119              -16.567328 -15.620894 -15.100422    -18.675322   

   children_education  government  mental_health    Tweet_topic  \
0          -18.814993  -15.527509      -6.028125  mental_health   
1          -20.749207  -15.545786      -7.749233  mental_health   
2          -20.613957  -15.545756      -6.854449  mental_health   
3          -20.620848  -15.135189     -10.086894  mental_health   
4          -20.613949  -15.545756      -8.601082  mental_health   

  Sentiment_Class  
0        Positive  
1        Negative  
2        Positive  
3        Negative  
4         Neutral

In [ ]:
df_result.tail()

symptoms  prevention    testing  treatment  economic_impact  \
441542 -18.475564  -19.405458 -18.387847   0.000000       -18.014653   
441543 -18.677917  -19.405471 -18.387847   0.000000       -18.015324   
441544   0.000000  -19.405458 -18.336570 -16.583170       -18.017835   
441545 -18.108379  -19.405545 -18.566656 -15.365728       -18.021048   
441546 -14.306460  -16.838903   0.000000 -16.603530       -18.042752   

           travel  vaccination  vaccination_opposition   policies     causes  \
441542 -17.496732   -21.116118              -16.564844 -15.620743 -15.110073   
441543 -17.497598   -20.509502              -16.568931 -15.620800 -15.115348   
441544 -17.497039   -20.306017              -16.566825 -15.620912 -15.107265   
441545 -17.497012   -22.345796              -16.583566 -15.621015 -15.129535   
441546 -17.430494   -20.529619              -16.591428 -15.587561 -15.109626   

        transmission  children_education  government  mental_health  \
441542    -18.074191          -20.614231  -15.545773      -8.584191   
441543    -18.675322          -20.600556  -15.532207      -8.600619   
441544    -16.954375          -20.614312  -15.545759      -6.693618   
441545    -23.866427          -20.615722  -15.529129     -11.477830   
441546    -17.394985          -20.615068  -15.545308      -4.193139   

          Tweet_topic  
441542      treatment  
441543      treatment  
441544       symptoms  
441545  mental_health  
441546        testing

In [ ]:
df_final_result[df_final_result.isnull().any(axis=1)]

Empty DataFrame
Columns: [id, UIN, week, user_id, clean_text, compound, lemma_2, symptoms, prevention, testing, treatment, economic_impact, travel, vaccination, vaccination_opposition, policies, causes, transmission, children_education, government, mental_health, Tweet_topic, Sentiment_Class]
Index: []

In [ ]:
df_final_result.loc[441451]

id                                                                                                                                                                                              1.4883687192984494e+18
UIN                                                                                                                                                                                                             441580
week                                                                                                                                                                                                           week_11
user_id                                                                                                                                                                                                     15561456.0
clean_text                a japanese conglomerate has found that the antiparasitic drug ivermectin is effective and safe for the treatment o

In [ ]:
df_final_result.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Corex_result_Set2.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_2'].tail(100)
df_s.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Sample_result/sample_Corex_result2.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_3'].tail(100)
df_s.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Sample_result/sample_Corex_result3.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_5'].tail(100)
df_s.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Sample_result/sample_Corex_result5.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_8'].tail(100)
df_s.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Sample_result/sample_Corex_result.csv")

In [ ]:
# For snippets
df_s = df_final_result[df_final_result['week']=='week_11'].tail(100)
df_s.to_csv("/content/drive/MyDrive/IDS 506 Healthcare Analytics/506 Project/Final_cleaned_tweets/Sample_result/sample_Corex_result11.csv")

## Code ends here

## Trial and error below this

In [ ]:
df_sample2 = df_result.iloc[0:1500]
mind = df_sample2.idxmax(axis=1)
df_sample2['new_label'] = mind
df_sample2.head(1000)
df_sample2['new_label'].value_counts()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


vaccination_opposition    1140
mental_health               86
vaccination                 70
government                  47
policies                    41
economic_impact             31
transmission                29
prevention                  27
testing                     12
symptoms                     8
children_education           6
treatment                    3
Name: new_label, dtype: int64

In [ ]:
pd.set_option("max_columns", 30)
pd.set_option("max_rows", 1000)
pd.set_option("max_colwidth", 400)


In [ ]:
df_sample = df_result.iloc[0:1500]
df_sample = round(df_sample, 6)
#df_sample['id'] = df_sample.index.astype(str)
#df_sample[(df_sample['cause'] <=0) & (df_sample['cause']>=-160)]
df_sample


symptoms  prevention    testing  treatment  mental_health  \
id                                                                         
1.462294e+18 -19.627056  -19.988126 -29.442190 -16.668713     -14.728888   
1.464266e+18 -19.627132  -19.988708 -29.443901 -11.201152     -14.727933   
1.464293e+18 -19.627157  -19.988660 -29.443900 -16.633330     -14.724822   
1.464293e+18 -19.627157  -19.988663 -29.443900 -16.632893     -13.057052   
1.464293e+18 -19.627157  -19.988660 -29.443900 -16.633330     -14.724822   
...                 ...         ...        ...        ...            ...   
1.464315e+18 -19.627326  -19.989193 -29.443901 -16.650432     -13.133623   
1.464315e+18 -19.627138  -19.988628 -29.443900 -16.635542     -14.728656   
1.464315e+18 -19.627131  -19.988651 -29.443900 -16.632595     -14.724489   
1.464315e+18 -19.627929    0.000000 -27.995845 -14.825308     -14.616357   
1.464315e+18 -19.627157  -19.988660 -29.443900 -16.633392     -14.724903   

              economic_impact  vaccination  vaccination_opposition   policies  \
id                                                                              
1.462294e+18       -15.805592   -21.930414              -12.012992 -15.552787   
1.464266e+18       -15.809738   -21.930420               -1.738986 -15.552749   
1.464293e+18       -15.806850   -21.930420               -4.353416 -15.552777   
1.464293e+18       -15.789158   -21.930420               -9.722623 -15.552752   
1.464293e+18       -15.806850   -21.930420               -7.552663 -15.552777   
...                       ...          ...                     ...        ...   
1.464315e+18       -15.807970   -21.930420               -6.472934 -15.502470   
1.464315e+18       -15.809375   -21.930420               -3.394506 -15.553144   
1.464315e+18       -15.750981   -21.930420               -0.019051 -15.552804   
1.464315e+18       -13.108194   -21.940902               -0.586956 -10.178069   
1.464315e+18       -15.789513   -21.930420               -6.202726 -15.552777   

                   cause  transmission  children_education  government  
id                                                                      
1.462294e+18 -193.493216    -17.119123          -14.975607  -15.761358  
1.464266e+18 -164.125199    -17.104329          -16.881934  -15.761427  
1.464293e+18 -141.065747    -17.119357          -16.875562  -15.761421  
1.464293e+18 -197.782648    -17.119357          -16.875386  -15.761421  
1.464293e+18 -141.065747    -17.119357          -16.875562  -15.761421  
...                  ...           ...                 ...         ...  
1.464315e+18 -127.497614    -17.119388          -16.880819  -15.761430  
1.464315e+18 -138.555849    -17.119356          -16.874833  -15.761421  
1.464315e+18 -152.262464    -17.119357          -16.875627  -15.761421  
1.464315e+18 -384.942506    -16.075088           -2.938404  -15.761415  
1.464315e+18 -174.726907    -17.119357          -16.875577  -15.761421  

[1500 rows x 13 columns]

In [ ]:
df_sample = df_sample.reset_index()
df_sample.head()
df_sample['id']=df_sample['id'].astype(str)
df_sample.head()
df_sample.dtypes
df_sample.head()

id   symptoms  prevention    testing  treatment  \
0   1.462294248007504e+18 -19.627056  -19.988126 -29.442190 -16.668713   
1  1.4642656149949522e+18 -19.627132  -19.988708 -29.443901 -11.201152   
2    1.46429253197022e+18 -19.627157  -19.988660 -29.443900 -16.633330   
3  1.4642925246678548e+18 -19.627157  -19.988663 -29.443900 -16.632893   
4  1.4642925159016776e+18 -19.627157  -19.988660 -29.443900 -16.633330   

   mental_health  economic_impact  vaccination  vaccination_opposition  \
0     -14.728888       -15.805592   -21.930414              -12.012992   
1     -14.727933       -15.809738   -21.930420               -1.738986   
2     -14.724822       -15.806850   -21.930420               -4.353416   
3     -13.057052       -15.789158   -21.930420               -9.722623   
4     -14.724822       -15.806850   -21.930420               -7.552663   

    policies       cause  transmission  children_education  government  
0 -15.552787 -193.493216    -17.119123          -14.975607  -15.761358  
1 -15.552749 -164.125199    -17.104329          -16.881934  -15.761427  
2 -15.552777 -141.065747    -17.119357          -16.875562  -15.761421  
3 -15.552752 -197.782648    -17.119357          -16.875386  -15.761421  
4 -15.552777 -141.065747    -17.119357          -16.875562  -15.761421

In [ ]:
#df_result[df_result['vaccination_opposition']==0]

symptoms  prevention    testing     treatment  \
id                                                                    
1464292753366528002 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464293608685809665 -18.902290  -20.095249 -33.756910 -5.756587e+00   
1464294903631028227 -18.846881  -20.095440 -33.756914 -6.755039e+00   
1464295099966410762 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464296162597421057 -18.846881  -20.095440 -33.756914 -4.880178e+00   
1464296228771049473 -18.946853  -20.096187 -33.761082 -8.735054e-05   
1464296374204305415 -18.946853  -20.096187 -33.761082 -8.735054e-05   
1464296498309566469 -18.946853  -20.096187 -33.761082 -8.735054e-05   
1464296443590680588 -18.946853  -20.096187 -33.761082 -8.735054e-05   
1464297240927911942 -18.847453  -20.095444 -33.756914 -5.811893e+00   
1464297417671688197 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464298142044676103 -18.846881  -20.095440 -33.756914 -6.755039e+00   
1464298334382866432 -18.919133  -20.099379 -33.756914 -6.758207e+00   
1464298711895396353 -18.846872  -20.095440 -33.756914 -6.755071e+00   
1464299205225324551 -18.846872  -20.095440 -33.756914 -6.755071e+00   
1464299737482416139 -18.923381  -16.835865 -33.757006 -2.528357e-08   
1464299675574358016 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464300275192242178 -18.862862  -20.098308 -33.756953 -5.808680e+00   
1464300759336452096 -18.969101  -20.100623 -33.763792 -3.016964e-11   
1464301400024883200 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464302503311425538 -18.910698  -20.095021 -33.756922 -6.012934e-08   
1464302440967249923 -18.901192  -20.095367 -33.756910 -5.760925e+00   
1464302737148063746 -18.926642  -20.135979 -33.757141 -3.521664e-01   
1464303612289593361 -18.908683  -20.095231   0.000000 -2.490896e-12   
1464305350627282952 -18.902369  -20.095416 -33.756914 -5.267498e+00   
1464307482289917958 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464307741900562436 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464309966655873026 -17.476859  -20.132018 -43.980666 -1.812153e+00   
1464310250996219912 -18.901518  -20.029804 -27.521633 -4.440892e-16   
1464311840540966913 -15.911979  -20.094353 -33.793194 -3.505975e-04   
1464312331924553728 -18.902988  -20.094831 -33.756910 -1.718593e-08   
1464312668521652236 -18.866277  -20.096070 -33.655548  0.000000e+00   
1464312618982653961 -16.209778  -20.095613 -33.756914 -5.809960e+00   
1464313910044024832 -18.907534  -20.098202 -29.468480 -4.440892e-16   
1464314364182237185   0.000000  -20.093370 -33.756910 -4.614120e-01   
1464316347869974537 -18.928280  -20.180119 -33.756917 -1.642280e-08   
1464316851262005251 -19.019243  -20.099061 -33.763420  0.000000e+00   
1464319675186270210 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464323209742848003 -18.959617  -20.101866 -31.098346 -4.499068e-12   
1464323519886422019 -18.881895  -20.095079 -33.756908 -1.647464e+00   
1464327863901966337 -18.906152  -20.094320 -33.756833 -1.481720e+00   
1464328181268336651 -18.905430  -20.095229 -33.756910 -1.304875e-01   
1464329359053967367 -18.884033  -20.095322 -31.250038 -4.204413e-08   
1464331420579635203 -18.911302  -20.095640 -33.756899 -4.160641e-01   
1464331448224256005 -18.940819  -20.093036 -33.761091  0.000000e+00   
1464332540571959303 -18.910417  -20.095484 -33.655533 -1.690514e-11   
1464332517834690567 -18.941154  -20.106532 -33.756757 -1.967503e-06   
1464332874237112322 -18.899712  -20.095278 -33.789896 -3.471907e-07   
1464333737286672395 -18.902059  -20.177139   0.000000 -2.329337e+00   
1464335726233874433 -18.918225  -20.095363 -33.756910 -2.323248e-07   
1464337045351014400 -15.883043  -20.112591 -33.750284  0.000000e+00   
1464337086081900544 -18.926554  -17.339722 -33.746728  0.000000e+00   
1464339820956708864 -18.846881  -20.095440 -33.756914 -5.811963e+00   
1464341591359987713 -18.834340  -20.095455 -33.756908 -2.299300e-09   
1464342097117409282   0.000000  -20.095357 -33

In [ ]:

result = pd.merge(df[['id', 'omicron_tweets', 'lemma_2']], df_cor,  on="id")
result.head()

In [ ]:
#Grouping the results by taking average of topic strength scores at user level
cor_grp = df_cor.groupby(['id'], as_index=False)['symptoms','prevention','testing','treatment','mental_health','economic_impact','vaccination', 
         'vaccination_opposition', 'policies', 'causes', 'transmission', 'children+Education', 'government'].mean()

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:2: FutureWarning: Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.
  


In [ ]:
cor_grp.head(50)

id  symptoms  prevention   testing  treatment  \
0   1462294248007503872  0.208388    0.130697 -0.120347  -0.386371   
1   1464265614994952192  0.216063    0.203719  0.211274   0.277068   
2   1464292515901677568  0.216063    0.226619  0.210932   0.277068   
3   1464292524667854848  0.216063    0.226621  0.210940   0.277068   
4   1464292531970220032  0.054052    0.226620  0.210932   0.277067   
5   1464292561443512320  0.216064   -0.589996  0.210245   0.277069   
6   1464292612207263744  0.216063   -0.485281  0.210849   0.277068   
7   1464292636521644032  0.216063    0.226671  0.210943   0.277068   
8   1464292642808815616  0.216063    0.130037  0.210932   0.277068   
9   1464292644507504640  0.216063    0.226619  0.210932   0.277068   
10  1464292675553742848  0.216063    0.226619  0.210932   0.277068   
11  1464292681413275648  0.216063    0.224653  0.211391  26.469243   
12  1464292710022623232  0.216063    0.226760  0.210866   0.277047   
13  1464292713688358912  0.216063   -0.686757  0.210994   0.277047   
14  1464292736312516608  0.216063    0.226747  0.210989   0.277068   
15  1464292737570775040  0.216063    0.226629  0.210935   0.277068   
16  1464292750883319808  0.216063    0.226598  0.210932   0.277068   
17  1464292753366528000  0.216063    0.224852  0.211368   0.277009   
18  1464292799025668096  0.216064   -1.303637  0.211375   0.277069   
19  1464292859557957632  0.216063   -0.070805  0.210933   0.271031   
20  1464292865308303360  0.216063    0.226760  0.210867   0.277047   
21  1464292876427444224  0.216063    0.227966  0.211104   0.277069   
22  1464292879556399104  0.216063    0.226628  0.210935   0.277068   
23  1464292924347371520  0.216063    0.130037  0.210932   0.277068   
24  1464293020044443648  0.216063    0.226598 -0.746635   0.277068   
25  1464293034531581952  0.216063    0.226625  0.210935   0.083052   
26  1464293037241036800  0.216063    0.226619  0.210932   0.277068   
27  1464293138596605952  0.216063    0.226681  1.955481   0.277068   
28  1464293139259301888  0.216046    0.225655  0.305315   0.277080   
29  1464293153901629440  0.216063    0.226631  0.210933   0.277068   
30  1464293251129786368  0.216063    0.224653  0.211391  26.469243   
31  1464293251721031680  0.216063    0.130064  0.210943   0.277068   
32  1464293262064291840  0.216063    0.226619  0.210932   0.277068   
33  1464293271337783296  0.216063    0.227836  0.210810   0.271031   
34  1464293303533375488  0.216063    0.226620  0.210932   0.277068   
35  1464293306293096448  0.216063    0.224653  0.211391  26.469243   
36  1464293329797988352  0.216063    0.130141  0.210995   0.277068   
37  1464293349167411200  0.216063    0.226964  0.210957   0.277068   
38  1464293373800423424  0.216040   -0.147288  0.211532   0.277089   
39  1464293468096897024  0.216062    0.226718  0.210827  -0.794737   
40  1464293608685809664  0.216063    0.226866  0.211078   0.277009   
41  1464293641699135488  0.216063   -1.316823  0.210878   0.277068   
42  1464293667569549312  0.216061    0.224614  0.211025  -0.644863   
43  1464293676188770304  0.216063    0.824543  0.210119   0.277068   
44  1464293682857889792  0.216063    0.226629  0.210935   0.277068   
45  1464293685143687168  0.216063    0.226619  0.210932   0.277068   
46  1464293717322444800  0.216063    0.226835  0.211039   0.277068   
47  1464293741531959296  0.216060   -0.537624  0.211146   0.276897   
48  1464293763820445696  0.216063    0.227436  0.208850   0.083053   
49  1464293821005582336  0.216046    0.128472 -0.202006   0.277059   

    mental_health  economic_impact  vaccination  vaccination_opposition  \
0        0.497062         0.193817     0.289194               -0.052470   
1        0.171803         0.193438     0.289194               -0.234824   
2        0.497062         0.323835     0.289194                0.156832   
3        0.497062         0.323835     0.289194                0.156832   
4        0.497062         0.323835     0.289194                0.156832   


In [ ]:
df.head()

created_at                   id  \
0  Sun Nov 21 05:38:11 +0000 2021  1462294248007503872   
1  Fri Nov 26 16:11:42 +0000 2021  1464265614994952192   
2  Fri Nov 26 17:58:39 +0000 2021  1464292531970220032   
3  Fri Nov 26 17:58:37 +0000 2021  1464292524667854848   
4  Fri Nov 26 17:58:35 +0000 2021  1464292515901677568   

                                                                                                                                                                                                       omicron_tweets  \
0  it was so nice to join @ubcaoii for initiation - the first in person one the chapter has held since the world closed down because of #covid19 @alphaomicronpi @aoiivancouver @aoii_calgary https://t.co/3apqzofbhm   
1                                                                                                new nu novel coronavirus sars-cov2 covid-19 variant.\n\ncouldn’t be easy like kappa or lambda or omicron or even pi.   
2                                                                                                                                              put away the "nu" jokes - the name is omicron. https://t.co/cgszlzk4cw   
3                                                                                                             @riochtconor2 breaking: who designates new coronavirus strain as a variant of concern, names it omicron   
4                                                                                                                                                                                     omicron https://t.co/m2vldtse5l   

                                                                                                                                       clean_text  \
0  it was so nice to join  for initiation  the first in person one the chapter has held since the world closed down because of covid19   calgary    
1                                     new nu novel coronavirus sarscov2 covid19 variantcouldnt be easy like kappa or lambda or omicron or even pi   
2                                                                                                     put away the nu jokes  the name is omicron    
3                                                         breaking who designates new coronavirus strain as a variant of concern names it omicron   
4                                                                                                                                        omicron    

   compound    neg    neu    pos  \
0    0.7253  0.000  0.798  0.202   
1    0.7717  0.000  0.661  0.339   
2    0.2500  0.000  0.800  0.200   
3   -0.0516  0.085  0.915  0.000   
4    0.0000  0.000  1.000  0.000   

                                                                                    clean_text2  \
0             nice join initiation first person chapter held since world closed covid19 calgary   
1  new novel coronavirus sarscov2 covid19 variantcouldnt easy like kappa lambda omicron even pi   
2                                                                        put away jokes omicron   
3                      breaking designates new coronavirus strain variant concern names omicron   
4                                                                                       omicron   

                                                                                                  tokenised_tweet  \
0                [nice, join, initiation, first, person, chapter, held, since, world, closed, covid, 19, calgary]   
1  [new, novel, coronavirus, sarscov, 2, covid, 19, variantcouldnt, easy, like, kappa, lambda, omicron, even, pi]   
2                                                                                     [put, away, jokes, omicron]   
3                              [breaking, designates, new, coronavirus, strain, variant, concern, names, omicron]   
4                                                                              

In [ ]:
print(df['lemma_2'].values.tolist())

['nice join initiation first person chapter hold since world close covid19 calgary', 'new novel coronavirus sarscov2 covid19 variantcouldnt easy like kappa lambda omicron even pi', 'put away joke omicron', 'break designate new coronavirus strain variant concern name omicron', 'omicron', 'shit call omicron', 'omicron', 'hailomicron', 'officially voc amp omicron', 'name omicron', 'get use hearing omicron', 'say preliminary evidence suggest late coronavirus variant carry high risk reinfection variant concern say number case omicron variant appear increase almost province south africa', 'omicron persei 8', 'b11529 call omicron variant concernfudge covid19covid19bc', 'base evidence present indicative detrimental change covid19 epidemiology tagve advise variant designate voc designate b11529 vocnamed omicron', 'designates new coronavirus strain variant concern name omicron', 'label newly identify covid strain omicron covidvariant covid19', 'omicron ncovid19 covidvariant sarscov2 pandemic', '

In [ ]:
#df.head(30)